In [0]:
# Databricks notebook: 04_gold_aggregations_features
# Default language: Python

from pyspark.sql import functions as F

catalog = "cscie103_catalog"
schema  = "final_project"

spark.sql(f"USE {catalog}.{schema}")

gdf = spark.table("gold_daily_store_family")

display(gdf.limit(10))

# =========================================
# 1. Daily rollups
# =========================================

# 1.1 Daily per store (aggregated across families)
gold_daily_store = (
    gdf.groupBy(
        "date",
        "store_nbr",
        "city",
        "state",
        "store_type",
        "cluster"
    )
    .agg(
        F.sum("sales").alias("total_sales"),
        F.sum("onpromotion").alias("total_onpromotion_items"),
        F.sum("transactions").alias("total_transactions"),
        F.avg("dcoilwtico").alias("avg_dcoilwtico"),
        F.max("is_holiday").alias("is_holiday")  # 1 if any family in that store-day is a holiday
    )
)

gold_daily_store.write.format("delta").mode("overwrite").saveAsTable("gold_daily_store")
print("✅ gold_daily_store written")

# 1.2 Daily per family (aggregated across stores)
gold_daily_family = (
    gdf.groupBy(
        "date",
        "family"
    )
    .agg(
        F.sum("sales").alias("total_sales"),
        F.sum("onpromotion").alias("total_onpromotion_items"),
        F.sum("transactions").alias("total_transactions"),
        F.avg("dcoilwtico").alias("avg_dcoilwtico"),
        F.max("is_holiday").alias("is_holiday")
    )
)

gold_daily_family.write.format("delta").mode("overwrite").saveAsTable("gold_daily_family")
print("✅ gold_daily_family written")

# =========================================
# 2. Monthly and yearly aggregations
# =========================================

# 2.1 Monthly per store-family
gold_monthly_store_family = (
    gdf
    .groupBy(
        F.date_trunc("month", "date").alias("month_start"),
        "store_nbr",
        "family"
    )
    .agg(
        F.sum("sales").alias("monthly_sales"),
        F.sum("onpromotion").alias("monthly_onpromotion_items"),
        F.sum("transactions").alias("monthly_transactions"),
        F.avg("dcoilwtico").alias("avg_monthly_oil_price"),
        F.max("is_holiday").alias("any_holiday_flag")
    )
)

gold_monthly_store_family.write.format("delta").mode("overwrite").saveAsTable("gold_monthly_store_family")
print("✅ gold_monthly_store_family written")

# 2.2 Monthly per store (for store-level performance / maps)
gold_monthly_store = (
    gdf
    .groupBy(
        F.date_trunc("month", "date").alias("month_start"),
        "store_nbr",
        "city",
        "state",
        "store_type",
        "cluster"
    )
    .agg(
        F.sum("sales").alias("monthly_sales"),
        F.sum("transactions").alias("monthly_transactions"),
        F.sum("onpromotion").alias("monthly_onpromotion_items"),
        F.avg("dcoilwtico").alias("avg_monthly_oil_price")
    )
)

gold_monthly_store.write.format("delta").mode("overwrite").saveAsTable("gold_monthly_store")
print("✅ gold_monthly_store written")

# 2.3 Yearly per store-family
gold_yearly_store_family = (
    gdf
    .groupBy(
        F.date_trunc("year", "date").alias("year_start"),
        "store_nbr",
        "family"
    )
    .agg(
        F.sum("sales").alias("yearly_sales"),
        F.sum("onpromotion").alias("yearly_onpromotion_items"),
        F.sum("transactions").alias("yearly_transactions"),
        F.avg("dcoilwtico").alias("avg_yearly_oil_price")
    )
)

gold_yearly_store_family.write.format("delta").mode("overwrite").saveAsTable("gold_yearly_store_family")
print("✅ gold_yearly_store_family written")

# =========================================
# 3. Store-level feature table
# =========================================

store_features = (
    gdf
    .groupBy("store_nbr", "city", "state", "store_type", "cluster")
    .agg(
        F.countDistinct("date").alias("num_days"),
        F.sum("sales").alias("total_sales"),
        F.avg("sales").alias("avg_daily_sales"),
        F.stddev("sales").alias("std_daily_sales"),
        F.sum("transactions").alias("total_transactions"),
        F.avg("transactions").alias("avg_daily_transactions"),
        (F.sum("sales") / F.sum(F.when(F.col("transactions") > 0, F.col("transactions")).otherwise(0.0))
         ).alias("avg_sales_per_transaction"),

        F.avg(F.when(F.col("onpromotion") > 0, F.col("sales")).otherwise(None)).alias("avg_sales_on_promo"),
        F.avg(F.when(F.col("onpromotion") == 0, F.col("sales")).otherwise(None)).alias("avg_sales_no_promo"),

        F.avg(F.when(F.col("is_holiday") == 1, F.col("sales")).otherwise(None)).alias("avg_sales_holiday"),
        F.avg(F.when(F.col("is_holiday") == 0, F.col("sales")).otherwise(None)).alias("avg_sales_nonholiday")
    )
    .withColumn(
        "promo_lift_pct",
        (F.col("avg_sales_on_promo") - F.col("avg_sales_no_promo")) / F.col("avg_sales_no_promo") * 100.0
    )
    .withColumn(
        "holiday_uplift_pct",
        (F.col("avg_sales_holiday") - F.col("avg_sales_nonholiday")) / F.col("avg_sales_nonholiday") * 100.0
    )
)

store_features.write.format("delta").mode("overwrite").saveAsTable("gold_store_features")
print("✅ gold_store_features written")

# =========================================
# 4. Family-level feature table
# =========================================

family_features = (
    gdf
    .groupBy("family")
    .agg(
        F.countDistinct("date").alias("num_days"),
        F.countDistinct("store_nbr").alias("num_stores_selling"),
        F.sum("sales").alias("total_sales"),
        F.avg("sales").alias("avg_daily_sales"),
        F.stddev("sales").alias("std_daily_sales"),
        F.sum("transactions").alias("total_transactions"),

        F.avg(F.when(F.col("onpromotion") > 0, F.col("sales")).otherwise(None)).alias("avg_sales_on_promo"),
        F.avg(F.when(F.col("onpromotion") == 0, F.col("sales")).otherwise(None)).alias("avg_sales_no_promo"),
        F.avg(F.when(F.col("is_holiday") == 1, F.col("sales")).otherwise(None)).alias("avg_sales_holiday"),
        F.avg(F.when(F.col("is_holiday") == 0, F.col("sales")).otherwise(None)).alias("avg_sales_nonholiday")
    )
    .withColumn(
        "promo_lift_pct",
        (F.col("avg_sales_on_promo") - F.col("avg_sales_no_promo")) / F.col("avg_sales_no_promo") * 100.0
    )
    .withColumn(
        "holiday_uplift_pct",
        (F.col("avg_sales_holiday") - F.col("avg_sales_nonholiday")) / F.col("avg_sales_nonholiday") * 100.0
    )
)

family_features.write.format("delta").mode("overwrite").saveAsTable("gold_family_features")
print("✅ gold_family_features written")

from pyspark.sql import functions as F

# =========================================
# 5. Calendar table for BI
# =========================================

# 5.1 Get min/max date from the Gold daily fact
min_max = (
    gdf.agg(
        F.min("date").alias("min_date"),
        F.max("date").alias("max_date")
    )
    .collect()[0]
)

start_date = min_max["min_date"]
end_date   = min_max["max_date"]

print(f"Building calendar from {start_date} to {end_date}")

# 5.2 Build continuous date range using sequence + explode
calendar_df = (
    spark.sql(f"""
      SELECT explode(
        sequence(
          to_date('{start_date}'),
          to_date('{end_date}'),
          interval 1 day
        )
      ) AS date
    """)
    .withColumn("year", F.year("date"))
    .withColumn("month", F.month("date"))
    .withColumn("day", F.dayofmonth("date"))
    .withColumn("day_of_week", F.date_format("date", "E"))   # Mon, Tue, Wed...
    .withColumn("week_of_year", F.weekofyear("date"))
    .withColumn("is_weekend", F.col("day_of_week").isin("Sat", "Sun").cast("int"))
    # Paydays: 15th and last day of month
    .withColumn(
        "is_payday",
        F.when(F.dayofmonth("date") == 15, 1)
         .when(F.dayofmonth("date") == F.dayofmonth(F.last_day("date")), 1)
         .otherwise(0)
    )
    # Earthquake period flag (example from Kaggle description: 2016-04-16 and weeks after)
    .withColumn(
        "is_earthquake_period",
        F.when(
            (F.col("date") >= F.to_date(F.lit("2016-04-16"))) &
            (F.col("date") <= F.to_date(F.lit("2016-05-31"))),
            1
        ).otherwise(0)
    )
)

display(calendar_df.limit(10))

# 5.3 Save as Gold calendar table
calendar_df.write.format("delta").mode("overwrite").saveAsTable("gold_calendar")
print("✅ gold_calendar written")

id date store_nbr family sales onpromotion transactions dcoilwtico city state store_type cluster is_holiday year month day week_of_year day_of_week is_weekend 0 2013-01-01 1 AUTOMOTIVE 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 1 2013-01-01 1 BABY CARE 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 2 2013-01-01 1 BEAUTY 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 3 2013-01-01 1 BEVERAGES 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 4 2013-01-01 1 BOOKS 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 5 2013-01-01 1 BREAD/BAKERY 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 6 2013-01-01 1 CELEBRATION 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 7 2013-01-01 1 CLEANING 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 8 2013-01-01 1 DAIRY 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0 9 2013-01-01 1 DELI 0.0 0 null null Quito Pichincha D 13 1 2013 1 1 1 3 0

✅ gold_daily_store written
✅ gold_daily_family written
✅ gold_monthly_store_family written
✅ gold_monthly_store written
✅ gold_yearly_store_family written
✅ gold_store_features written
✅ gold_family_features written
Building calendar from 2013-01-01 to 2017-08-15


date year month day day_of_week week_of_year is_weekend is_payday is_earthquake_period 2013-01-01 2013 1 1 Tue 1 0 0 0 2013-01-02 2013 1 2 Wed 1 0 0 0 2013-01-03 2013 1 3 Thu 1 0 0 0 2013-01-04 2013 1 4 Fri 1 0 0 0 2013-01-05 2013 1 5 Sat 1 1 0 0 2013-01-06 2013 1 6 Sun 1 1 0 0 2013-01-07 2013 1 7 Mon 2 0 0 0 2013-01-08 2013 1 8 Tue 2 0 0 0 2013-01-09 2013 1 9 Wed 2 0 0 0 2013-01-10 2013 1 10 Thu 2 0 0 0

✅ gold_calendar written


In [0]:
%sql
SELECT *
FROM gold_daily_store
ORDER BY date DESC, total_sales DESC
LIMIT 50;

date store_nbr city state store_type cluster total_sales total_onpromotion_items total_transactions avg_dcoilwtico is_holiday 2017-08-15 44 Quito Pichincha A 5 33141.322 168 125895 47.56999999999999 1 2017-08-15 47 Quito Pichincha A 14 31653.691000000006 178 118173 47.56999999999999 1 2017-08-15 45 Quito Pichincha A 11 31562.926000000003 172 121605 47.56999999999999 1 2017-08-15 3 Quito Pichincha D 8 30185.60200000001 143 97548 47.56999999999999 1 2017-08-15 49 Quito Pichincha A 11 28429.226003 168 92862 47.56999999999999 1 2017-08-15 46 Quito Pichincha A 14 22348.414969999998 163 105501 47.56999999999999 1 2017-08-15 11 Cayambe Pichincha B 6 21727.24 335 77880 47.56999999999999 1 2017-08-15 51 Guayaquil Guayas A 17 20154.559 127 51909 47.56999999999999 1 2017-08-15 40 Machala El Oro C 3 19552.934999999998 271 45936 47.56999999999999 1 2017-08-15 7 Quito Pichincha D 8 18744.295980000003 130 58740 47.56999999999999 1 2017-08-15 9 Quito Pichincha B 6 18636.477 331 71115 47.56999999999999 1 2017-08-15 52 Manta Manabi A 11 18600.046 142 74415 47.56999999999999 1 2017-08-15 8 Quito Pichincha D 8 17723.876000000004 137 86493 47.56999999999999 1 2017-08-15 48 Quito Pichincha A 14 17695.05 152 89826 47.56999999999999 1 2017-08-15 28 Guayaquil Guayas E 10 16879.197999999997 319 44319 47.56999999999999 1 2017-08-15 50 Ambato Tungurahua A 14 16879.121004 150 92532 47.56999999999999 1 2017-08-15 24 Guayaquil Guayas D 1 15866.394995000002 134 70554 47.56999999999999 1 2017-08-15 29 Guayaquil Guayas E 10 15659.655 352 42966 47.56999999999999 1 2017-08-15 31 Babahoyo Los Rios B 10 15469.877 296 44880 47.56999999999999 1 2017-08-15 43 Esmeraldas Esmeraldas E 10 15368.844000000001 290 48906 47.56999999999999 1 2017-08-15 39 Cuenca Azuay B 6 15008.64799 357 47025 47.56999999999999 1 2017-08-15 36 Libertad Guayas E 10 14986.342 330 39336 47.56999999999999 1 2017-08-15 20 Quito Pichincha B 6 14739.689 306 50028 47.56999999999999 1 2017-08-15 17 Quito Pichincha C 12 14123.768 268 49632 47.56999999999999 1 2017-08-15 21 Santo Domingo Santo Domingo de los Tsachilas B 6 14117.960000000003 299 34947 47.56999999999999 1 2017-08-15 6 Quito Pichincha D 13 13849.208995000003 135 52437 47.56999999999999 1 2017-08-15 27 Daule Guayas D 1 13377.979 118 50919 47.56999999999999 1 2017-08-15 54 El Carmen Manabi C 3 12666.858 204 26466 47.56999999999999 1 2017-08-15 33 Quevedo Los Rios C 3 11649.571 258 30327 47.56999999999999 1 2017-08-15 37 Cuenca Azuay D 2 11533.554995999999 129 45309 47.56999999999999 1 2017-08-15 34 Guayaquil Guayas B 6 11321.420995999999 258 66231 47.56999999999999 1 2017-08-15 18 Quito Pichincha B 16 11286.322 340 44319 47.56999999999999 1 2017-08-15 2 Quito Pichincha D 13 11196.260001999999 118 57321 47.56999999999999 1 2017-08-15 30 Guayaquil Guayas C 3 10982.768999999998 227 27225 47.56999999999999 1 2017-08-15 38 Loja Loja D 4 9966.252 120 47685 47.56999999999999 1 2017-08-15 1 Quito Pichincha D 13 9823.551018 115 55869 47.56999999999999 1 2017-08-15 4 Quito Pichincha D 9 9709.086000000001 119 42339 47.56999999999999 1 2017-08-15 41 Machala El Oro D 4 9397.724 123 33099 47.56999999999999 1 2017-08-15 14 Riobamba Chimborazo C 7 9342.731999999998 215 40953 47.56999999999999 1 2017-08-15 19 Guaranda Bolivar C 15 9282.187000000002 209 38214 47.56999999999999 1 2017-08-15 42 Cuenca Azuay D 2 9251.76999 119 32835 47.56999999999999 1 2017-08-15 5 Santo Domingo Santo Domingo de los Tsachilas D 4 8703.693000000001 107 43230 47.56999999999999 1 2017-08-15 53 Manta Manabi D 13 8208.189 114 30756 47.56999999999999 1 2017-08-15 15 Ibarra Imbabura C 15 7946.4310000000005 245 43560 47.56999999999999 1 2017-08-15 16 Santo Domingo Santo Domingo de los Tsachilas C 3 7487.428000000001 215 24486 47.56999999999999 1 2017-08-15 23 Ambato Tungurahua D 9 7371.562 93 31218 47.56999999999999 1 2017-08-15 12 Latacunga Cotopaxi C 15 6933.045 196 36168 47.56999999999999 1 2017-08-15 22 Puyo Pastaza C 7 6917.78799 228 25278 47.56999999999999 1 2017-08-15 10 Quito P

In [0]:
%sql
SELECT *
FROM gold_daily_family
ORDER BY date DESC, total_sales DESC;

date family total_sales total_onpromotion_items total_transactions avg_dcoilwtico is_holiday 2017-08-15 GROCERY I 224208.125 2296 86561 47.570000000000014 1 2017-08-15 BEVERAGES 170773.0 982 86561 47.570000000000014 1 2017-08-15 PRODUCE 125108.971 3169 86561 47.570000000000014 1 2017-08-15 CLEANING 58474.0 841 86561 47.570000000000014 1 2017-08-15 DAIRY 40707.0 977 86561 47.570000000000014 1 2017-08-15 BREAD/BAKERY 29158.19502000001 512 86561 47.570000000000014 1 2017-08-15 MEATS 17928.170943999998 0 86561 47.570000000000014 1 2017-08-15 POULTRY 17586.709986 6 86561 47.570000000000014 1 2017-08-15 DELI 14935.453000000001 341 86561 47.570000000000014 1 2017-08-15 PERSONAL CARE 14787.0 476 86561 47.570000000000014 1 2017-08-15 HOME CARE 13644.0 331 86561 47.570000000000014 1 2017-08-15 EGGS 9624.0 30 86561 47.570000000000014 1 2017-08-15 FROZEN FOODS 5309.611004000001 39 86561 47.570000000000014 1 2017-08-15 PREPARED FOODS 4641.52298 9 86561 47.570000000000014 1 2017-08-15 LIQUOR,WINE,BEER 3461.0 198 86561 47.570000000000014 1 2017-08-15 SCHOOL AND OFFICE SUPPLIES 2530.0 148 86561 47.570000000000014 1 2017-08-15 HOME AND KITCHEN I 1669.0 37 86561 47.570000000000014 1 2017-08-15 HOME AND KITCHEN II 1448.0 67 86561 47.570000000000014 1 2017-08-15 GROCERY II 1300.0 0 86561 47.570000000000014 1 2017-08-15 SEAFOOD 970.177005 0 86561 47.570000000000014 1 2017-08-15 LAWN AND GARDEN 679.0 25 86561 47.570000000000014 1 2017-08-15 CELEBRATION 597.0 0 86561 47.570000000000014 1 2017-08-15 PLAYERS AND ELECTRONICS 592.0 5 86561 47.570000000000014 1 2017-08-15 LADIESWEAR 503.0 26 86561 47.570000000000014 1 2017-08-15 MAGAZINES 461.0 0 86561 47.570000000000014 1 2017-08-15 LINGERIE 458.0 34 86561 47.570000000000014 1 2017-08-15 PET SUPPLIES 364.0 0 86561 47.570000000000014 1 2017-08-15 BEAUTY 339.0 55 86561 47.570000000000014 1 2017-08-15 AUTOMOTIVE 337.0 1 86561 47.570000000000014 1 2017-08-15 HARDWARE 57.0 0 86561 47.570000000000014 1 2017-08-15 BABY CARE 8.0 0 86561 47.570000000000014 1 2017-08-15 HOME APPLIANCES 3.0 0 86561 47.570000000000014 1 2017-08-15 BOOKS 0.0 0 86561 47.570000000000014 1 2017-08-14 GROCERY I 225355.694 2335 85448 47.59 0 2017-08-14 BEVERAGES 174832.0 957 85448 47.59 0 2017-08-14 PRODUCE 115257.59598000004 325 85448 47.59 0 2017-08-14 CLEANING 55032.0 840 85448 47.59 0 2017-08-14 DAIRY 43050.0 978 85448 47.59 0 2017-08-14 BREAD/BAKERY 28002.457000000002 490 85448 47.59 0 2017-08-14 POULTRY 18597.50806 7 85448 47.59 0 2017-08-14 MEATS 16975.686039999997 0 85448 47.59 0 2017-08-14 PERSONAL CARE 15077.0 471 85448 47.59 0 2017-08-14 DELI 14662.741 356 85448 47.59 0 2017-08-14 EGGS 14600.0 390 85448 47.59 0 2017-08-14 HOME CARE 13818.0 312 85448 47.59 0 2017-08-14 FROZEN FOODS 5422.669 41 85448 47.59 0 2017-08-14 PREPARED FOODS 4647.375001999999 8 85448 47.59 0 2017-08-14 LIQUOR,WINE,BEER 2839.0 179 85448 47.59 0 2017-08-14 SCHOOL AND OFFICE SUPPLIES 2826.0 154 85448 47.59 0 2017-08-14 HOME AND KITCHEN I 1682.0 23 85448 47.59 0 2017-08-14 HOME AND KITCHEN II 1668.0 65 85448 47.59 0 2017-08-14 GROCERY II 1371.0 0 85448 47.59 0 2017-08-14 SEAFOOD 970.6799987999999 0 85448 47.59 0 2017-08-14 LAWN AND GARDEN 654.0 0 85448 47.59 0 2017-08-14 CELEBRATION 594.0 0 85448 47.59 0 2017-08-14 PLAYERS AND ELECTRONICS 500.0 0 85448 47.59 0 2017-08-14 LADIESWEAR 487.0 31 85448 47.59 0 2017-08-14 MAGAZINES 457.0 0 85448 47.59 0 2017-08-14 LINGERIE 418.0 31 85448 47.59 0 2017-08-14 PET SUPPLIES 417.0 0 85448 47.59 0 2017-08-14 BEAUTY 337.0 50 85448 47.59 0 2017-08-14 AUTOMOTIVE 292.0 0 85448 47.59 0 2017-08-14 HARDWARE 66.0 0 85448 47.59 0 2017-08-14 BABY CARE 9.0 0 85448 47.59 0 2017-08-14 HOME APPLIANCES 4.0 0 85448 47.59 0 2017-08-14 BOOKS 0.0 0 85448 47.59 0 2017-08-13 GROCERY I 258442.45200000002 2320 85993 null 0 2017-08-13 BEVERAGES 202354.0 986 85993 null 0 2017-08-13 PRODUCE 125923.80240000002 319 85993 null 0 2017-08-13 CLEANING 61757.0 918 85993 null 0 2017-08-13 DAIRY 50112.0 997 85993 null 0 2017-08-13 BREAD/BAKERY 33262.757 1

In [0]:
%sql
SELECT *
FROM gold_monthly_store_family
ORDER BY month_start DESC, monthly_sales DESC;

month_start store_nbr family monthly_sales monthly_onpromotion_items monthly_transactions avg_monthly_oil_price any_holiday_flag 2017-08-01T00:00:00.000Z 45 GROCERY I 164681.0 666 58745 48.902727272727276 1 2017-08-01T00:00:00.000Z 47 GROCERY I 152173.0 680 57541 48.902727272727276 1 2017-08-01T00:00:00.000Z 44 GROCERY I 143052.0 650 64335 48.902727272727276 1 2017-08-01T00:00:00.000Z 46 GROCERY I 140431.0 670 52733 48.902727272727276 1 2017-08-01T00:00:00.000Z 44 PRODUCE 139693.164 620 64335 48.902727272727276 1 2017-08-01T00:00:00.000Z 44 BEVERAGES 136453.0 208 64335 48.902727272727276 1 2017-08-01T00:00:00.000Z 45 BEVERAGES 130901.0 219 58745 48.902727272727276 1 2017-08-01T00:00:00.000Z 47 BEVERAGES 128260.0 185 57541 48.902727272727276 1 2017-08-01T00:00:00.000Z 48 GROCERY I 127820.0 636 45595 48.902727272727276 1 2017-08-01T00:00:00.000Z 11 GROCERY I 119260.91400000002 1002 35268 48.902727272727276 1 2017-08-01T00:00:00.000Z 3 BEVERAGES 118177.0 176 46522 48.902727272727276 1 2017-08-01T00:00:00.000Z 3 PRODUCE 116024.43980000001 558 46522 48.902727272727276 1 2017-08-01T00:00:00.000Z 3 GROCERY I 115190.0 555 46522 48.902727272727276 1 2017-08-01T00:00:00.000Z 49 GROCERY I 115130.0 643 44677 48.902727272727276 1 2017-08-01T00:00:00.000Z 49 PRODUCE 111032.58200000001 633 44677 48.902727272727276 1 2017-08-01T00:00:00.000Z 9 GROCERY I 107185.56999999999 1030 30605 48.902727272727276 1 2017-08-01T00:00:00.000Z 50 GROCERY I 101120.0 604 41586 48.902727272727276 1 2017-08-01T00:00:00.000Z 49 BEVERAGES 98380.0 197 44677 48.902727272727276 1 2017-08-01T00:00:00.000Z 20 GROCERY I 97693.08799999999 962 24782 48.902727272727276 1 2017-08-01T00:00:00.000Z 45 PRODUCE 97488.33529999999 601 58745 48.902727272727276 1 2017-08-01T00:00:00.000Z 40 GROCERY I 96047.0 926 20197 48.902727272727276 1 2017-08-01T00:00:00.000Z 52 GROCERY I 94366.0 631 35818 48.902727272727276 1 2017-08-01T00:00:00.000Z 28 GROCERY I 87569.67900000002 891 19230 48.902727272727276 1 2017-08-01T00:00:00.000Z 46 BEVERAGES 87188.0 178 52733 48.902727272727276 1 2017-08-01T00:00:00.000Z 47 PRODUCE 85825.36600000001 578 57541 48.902727272727276 1 2017-08-01T00:00:00.000Z 51 PRODUCE 84688.649 574 25268 48.902727272727276 1 2017-08-01T00:00:00.000Z 39 GROCERY I 81721.79 1044 20779 48.902727272727276 1 2017-08-01T00:00:00.000Z 40 BEVERAGES 80565.0 414 20197 48.902727272727276 1 2017-08-01T00:00:00.000Z 43 BEVERAGES 79375.0 369 22869 48.902727272727276 1 2017-08-01T00:00:00.000Z 51 GROCERY I 76555.0 555 25268 48.902727272727276 1 2017-08-01T00:00:00.000Z 43 GROCERY I 75881.453 840 22869 48.902727272727276 1 2017-08-01T00:00:00.000Z 31 GROCERY I 74235.24799999999 988 20738 48.902727272727276 1 2017-08-01T00:00:00.000Z 52 PRODUCE 74175.96800000001 533 35818 48.902727272727276 1 2017-08-01T00:00:00.000Z 11 BEVERAGES 74023.0 455 35268 48.902727272727276 1 2017-08-01T00:00:00.000Z 7 PRODUCE 72341.51 553 25594 48.902727272727276 1 2017-08-01T00:00:00.000Z 48 BEVERAGES 72077.0 172 45595 48.902727272727276 1 2017-08-01T00:00:00.000Z 8 GROCERY I 71361.0 549 39657 48.902727272727276 1 2017-08-01T00:00:00.000Z 21 GROCERY I 70402.58400000002 984 17123 48.902727272727276 1 2017-08-01T00:00:00.000Z 6 GROCERY I 70370.0 591 25619 48.902727272727276 1 2017-08-01T00:00:00.000Z 8 PRODUCE 68177.553 606 39657 48.902727272727276 1 2017-08-01T00:00:00.000Z 17 GROCERY I 67841.0 847 22012 48.902727272727276 1 2017-08-01T00:00:00.000Z 51 BEVERAGES 67396.0 192 25268 48.902727272727276 1 2017-08-01T00:00:00.000Z 20 BEVERAGES 67382.0 485 24782 48.902727272727276 1 2017-08-01T00:00:00.000Z 52 BEVERAGES 67343.0 195 35818 48.902727272727276 1 2017-08-01T00:00:00.000Z 8 BEVERAGES 67057.0 186 39657 48.902727272727276 1 2017-08-01T00:00:00.000Z 50 BEVERAGES 65350.0 190 41586 48.902727272727276 1 2017-08-01T00:00:00.000Z 29 GROCERY I 63467.35999999999 1010 18175 48.902727272727276 1 2017-08-01T00:00:00.000Z 34 GROCERY I 63235.187 899 31247 48.902727272727276 1 2017-08-01T00:00:00.000Z 36 GROCERY I 61931.296 8

In [0]:
%sql
SELECT *
FROM gold_store_features
ORDER BY total_sales DESC;

store_nbr city state store_type cluster num_days total_sales avg_daily_sales std_daily_sales total_transactions avg_daily_transactions avg_sales_per_transaction avg_sales_on_promo avg_sales_no_promo avg_sales_holiday avg_sales_nonholiday promo_lift_pct holiday_uplift_pct 44 Quito Pichincha A 5 1684 6.3356137229998976E7 1120.1184051129553 2691.663957182299 244741167 4344.697715289983 0.25886996456954453 2781.8325472271504 546.267166396499 1214.2719646854828 1101.9691107485924 409.2439594306503 10.191107249875685 45 Quito Pichincha A 11 1684 5.568902200246001E7 984.5659984169586 2401.3758856243603 208735461 3705.516695957821 0.2667923396229259 2496.220888821761 448.55770482242065 1098.79757960442 962.5464103940449 456.49938948434493 14.155283084438178 47 Quito Pichincha A 14 1684 5.202447595600099E7 919.7778712916975 2230.0309008321105 219915663 3903.9900410076157 0.23656557812346904 2321.316154595245 411.38003981147295 1008.2955379702439 902.7149668588811 464.2753488134856 11.695892389902951 3 Quito Pichincha D 8 1684 5.1533528135851E7 911.0980540972915 2152.1393441221085 180583425 3207.634818288394 0.28537241519176526 2395.589058539299 420.6671422431085 976.4273055877915 898.5050111864574 469.4737758136716 8.672438487398 49 Quito Pichincha A 11 1684 4.434682276006599E7 784.0391563252005 1904.1514723306873 154116468 2735.908611599297 0.2877487612814095 2136.191737510336 331.9393537080847 865.914677535718 768.2566097870563 543.5488030108517 12.711646929498002 46 Quito Pichincha A 14 1684 4.2804727293645196E7 756.7753490620062 1895.8455871498097 201725469 3581.0738137082603 0.21219297447088942 1869.4327168783743 338.6729562569309 858.7576187599824 737.1169713957993 451.9875981653958 16.502217705535294 48 Quito Pichincha A 14 1684 3.6741804099816516E7 649.584599197633 1676.2929318751667 172072263 3054.6637375512596 0.21352543088142287 1627.074526200671 285.6346666522953 747.6381200317252 630.6835377703234 469.63482243607285 18.544099418683935 51 Guayaquil Guayas A 17 1684 3.360386127734599E7 594.1066666197446 1356.2981823349262 96734253 1717.2472173403632 0.34738327154235626 1545.6375567538746 307.3316365972666 643.263892545564 584.630987022353 402.92172126077224 10.02904512842204 8 Quito Pichincha D 8 1684 3.1124067145028997E7 550.2646148479367 1279.364914301214 155944800 2769.9882766705746 0.19958387291547391 1481.21274414179 257.842824316528 586.3573261508586 543.3072863643533 474.46343448497623 7.923700062000462 50 Ambato Tungurahua A 14 1684 2.927375099657431E7 517.5515539863213 1286.4590415433377 147630153 2620.7621558289397 0.19829113769579518 1343.2155861467138 232.89464781771233 572.7777533644896 506.9060026796041 476.74815575755713 12.99486499206452 11 Cayambe Pichincha B 6 1684 2.8906533919296E7 511.05926097549593 1365.9163771666144 133619574 2373.4337631887456 0.21633457624476485 1543.2254262790307 237.7675286045929 553.7725855883381 502.82572519417556 549.0480156545735 10.132110956432953 7 Quito Pichincha D 8 1684 2.7464557400119998E7 485.5655280951875 1140.3253873173849 100728012 1790.2428152492669 0.27266057231547464 1364.9128682870933 245.6283923788509 500.19804642391415 482.74492435332445 455.68204272651303 3.6153921439918935 9 Quito Pichincha B 6 1684 2.6969879523669496E7 476.81976457108124 1275.0391558506576 118270152 2100.7878077373975 0.22803622949321564 1384.8481012501616 214.57219313973837 522.8540183980199 467.9460775077119 545.3996116581101 11.733817960981433 6 Quito Pichincha D 13 1684 2.5720786244983003E7 454.7361522750787 1076.1852177214726 103222977 1833.510550996483 0.2491769467662515 1204.0693275422425 202.0649525106503 498.76902107723447 446.2482575929651 495.88232030429884 11.769404718253252 24 Guayaquil Guayas D 1 1684 2.423379351567E7 428.44654566086774 1021.5105015862192 119754525 2263.833437305053 0.20236223654738728 1213.504278741312 202.6814624127797 436.0845348611749 426.97422623951405 498.72484848658604 2.1336905278564458 2 Quito Pichincha D 13 1684 2.2026881902564194E7 389.42897886503647 1

In [0]:
%sql
SELECT *
FROM gold_family_features
ORDER BY total_sales DESC;

family num_days num_stores_selling total_sales avg_daily_sales std_daily_sales total_transactions avg_sales_on_promo avg_sales_no_promo avg_sales_holiday avg_sales_nonholiday promo_lift_pct holiday_uplift_pct GROCERY I 1684 54 3.5082729799000514E8 3790.4327973335617 2903.6999741165228 144262952 4426.943571433489 2717.34138897272 4189.966893769218 3713.417526134709 62.91451598236897 12.833174946813699 BEVERAGES 1684 54 2.2166354E8 2394.9127014996325 2316.775067180202 144262952 3224.894336480784 1290.3258455262032 2633.358202968311 2348.9493028170828 149.928678687022 12.107919903172805 PRODUCE 1684 54 1.2544796802497062E8 1355.3736983552726 2189.741018068485 144262952 2434.579491118157 794.3993375063012 1525.0925814068705 1322.658228205445 206.46796594273917 15.305114267960523 CLEANING 1684 54 9.9421019E7 1074.1715177838282 736.7841670700276 144262952 1242.3257814796668 867.5771351520551 1120.5572937558497 1065.2300703626381 43.19485048000161 5.193922414749002 DAIRY 1684 54 6.5823605E7 711.175990751545 674.0652428519559 144262952 935.5534230270569 479.19555233260814 764.3955742746357 700.9172401350551 95.2341624359844 9.05646637074434 BREAD/BAKERY 1684 54 4.2959924004929096E7 464.15061157492863 369.04952654255123 144262952 576.5095401801594 379.39264803137115 473.0086606698093 462.44311011405006 51.955907203686536 2.284724396294603 POULTRY 1684 54 3.249445088882909E7 351.0788159474166 400.8667893257101 144262952 486.0896972391841 313.3226587229422 378.0208424064721 345.88539818182045 55.14029506209839 9.290777926323198 MEATS 1684 54 3.16509962860629E7 341.96590481506223 454.0823812288984 144262952 465.84418450408157 302.94935939579676 351.0291196266812 340.2188550566637 53.769654913006846 3.1774442860367236 PERSONAL CARE 1684 54 2.5100482E7 271.1923808289036 228.1703423579115 144262952 340.1985828302466 220.73617761484363 294.5421179302046 266.6914224593417 54.119993607866846 10.443041329950855 DELI 1684 54 2.458562680473691E7 265.6297463669228 210.77412288548007 144262952 322.502658458386 221.74795941470265 280.1288864631637 262.8348529732877 45.43658453932225 6.579809828962693 HOME CARE 1684 54 1.6409522E7 177.2929037555642 210.75699764513033 144262952 310.82414257900257 101.95294992479424 207.1975531488167 171.52840279388644 204.8701806159434 20.79489447458527 EGGS 1684 54 1.5881196E7 171.58472708414365 161.84781497856218 144262952 210.03699198626217 154.94771221596187 178.18805990105628 170.31185082089743 35.55346444452072 4.624580757120411 FROZEN FOODS 1684 54 1.4646939998968437E7 158.2494921881719 340.9110702855436 144262952 235.11142797547643 107.74989175388049 246.8261346437434 141.1752194253383 118.20108043589674 74.83672817967849 PREPARED FOODS 1684 54 8966728.108912462 96.87895013734888 104.72327043509215 144262952 114.64666050361566 92.59640305309115 99.60328948245102 96.35379912928155 23.813298058545275 3.3724569062497456 LIQUOR,WINE,BEER 1684 54 7937172.0 85.75534811357448 127.3163913189876 144262952 121.33039333844637 77.01551775187747 114.17509025270758 80.2770818835537 57.540190444916675 42.22625881982704 SEAFOOD 1684 54 2051636.098841214 22.166430040637174 32.62287060005821 144262952 35.49316869300157 19.176353788467537 22.22577695117664 22.15499016992057 85.08820333898304 0.31950716616510777 GROCERY II 1684 54 2004966.0 21.662193698949824 31.092081321679697 144262952 27.252189949285384 21.387313246729693 25.00882470918572 21.017088069280135 27.422222861267915 18.992814926346306 HOME AND KITCHEN I 1684 54 1905076.0 20.58295518388867 36.153980753835995 144262952 39.70592943373574 16.886466485308716 23.9975264072737 19.924753215289055 135.13462374310242 20.440771074943324 HOME AND KITCHEN II 1684 54 1556511.0 16.816964864514457 31.513599178672134 144262952 41.34355261130796 10.281843930873118 18.504813477737667 16.491610608520837 302.1025108849044 12.207436356620342 CELEBRATION 1684 54 779502.0 8.421949954622066 15.957330320972828 144262952 20.15281582952816 7.990276797616247 9.774903061906672 8.161151060594346 1

In [0]:
%sql
SELECT *
FROM gold_family_features
ORDER BY total_sales DESC;

family num_days num_stores_selling total_sales avg_daily_sales std_daily_sales total_transactions avg_sales_on_promo avg_sales_no_promo avg_sales_holiday avg_sales_nonholiday promo_lift_pct holiday_uplift_pct GROCERY I 1684 54 3.5082729799000514E8 3790.4327973335617 2903.6999741165228 144262952 4426.943571433489 2717.34138897272 4189.966893769218 3713.417526134709 62.91451598236897 12.833174946813699 BEVERAGES 1684 54 2.2166354E8 2394.9127014996325 2316.775067180202 144262952 3224.894336480784 1290.3258455262032 2633.358202968311 2348.9493028170828 149.928678687022 12.107919903172805 PRODUCE 1684 54 1.2544796802497062E8 1355.3736983552726 2189.741018068485 144262952 2434.579491118157 794.3993375063012 1525.0925814068705 1322.658228205445 206.46796594273917 15.305114267960523 CLEANING 1684 54 9.9421019E7 1074.1715177838282 736.7841670700276 144262952 1242.3257814796668 867.5771351520551 1120.5572937558497 1065.2300703626381 43.19485048000161 5.193922414749002 DAIRY 1684 54 6.5823605E7 711.175990751545 674.0652428519559 144262952 935.5534230270569 479.19555233260814 764.3955742746357 700.9172401350551 95.2341624359844 9.05646637074434 BREAD/BAKERY 1684 54 4.2959924004929096E7 464.15061157492863 369.04952654255123 144262952 576.5095401801594 379.39264803137115 473.0086606698093 462.44311011405006 51.955907203686536 2.284724396294603 POULTRY 1684 54 3.249445088882909E7 351.0788159474166 400.8667893257101 144262952 486.0896972391841 313.3226587229422 378.0208424064721 345.88539818182045 55.14029506209839 9.290777926323198 MEATS 1684 54 3.16509962860629E7 341.96590481506223 454.0823812288984 144262952 465.84418450408157 302.94935939579676 351.0291196266812 340.2188550566637 53.769654913006846 3.1774442860367236 PERSONAL CARE 1684 54 2.5100482E7 271.1923808289036 228.1703423579115 144262952 340.1985828302466 220.73617761484363 294.5421179302046 266.6914224593417 54.119993607866846 10.443041329950855 DELI 1684 54 2.458562680473691E7 265.6297463669228 210.77412288548007 144262952 322.502658458386 221.74795941470265 280.1288864631637 262.8348529732877 45.43658453932225 6.579809828962693 HOME CARE 1684 54 1.6409522E7 177.2929037555642 210.75699764513033 144262952 310.82414257900257 101.95294992479424 207.1975531488167 171.52840279388644 204.8701806159434 20.79489447458527 EGGS 1684 54 1.5881196E7 171.58472708414365 161.84781497856218 144262952 210.03699198626217 154.94771221596187 178.18805990105628 170.31185082089743 35.55346444452072 4.624580757120411 FROZEN FOODS 1684 54 1.4646939998968437E7 158.2494921881719 340.9110702855436 144262952 235.11142797547643 107.74989175388049 246.8261346437434 141.1752194253383 118.20108043589674 74.83672817967849 PREPARED FOODS 1684 54 8966728.108912462 96.87895013734888 104.72327043509215 144262952 114.64666050361566 92.59640305309115 99.60328948245102 96.35379912928155 23.813298058545275 3.3724569062497456 LIQUOR,WINE,BEER 1684 54 7937172.0 85.75534811357448 127.3163913189876 144262952 121.33039333844637 77.01551775187747 114.17509025270758 80.2770818835537 57.540190444916675 42.22625881982704 SEAFOOD 1684 54 2051636.098841214 22.166430040637174 32.62287060005821 144262952 35.49316869300157 19.176353788467537 22.22577695117664 22.15499016992057 85.08820333898304 0.31950716616510777 GROCERY II 1684 54 2004966.0 21.662193698949824 31.092081321679697 144262952 27.252189949285384 21.387313246729693 25.00882470918572 21.017088069280135 27.422222861267915 18.992814926346306 HOME AND KITCHEN I 1684 54 1905076.0 20.58295518388867 36.153980753835995 144262952 39.70592943373574 16.886466485308716 23.9975264072737 19.924753215289055 135.13462374310242 20.440771074943324 HOME AND KITCHEN II 1684 54 1556511.0 16.816964864514457 31.513599178672134 144262952 41.34355261130796 10.281843930873118 18.504813477737667 16.491610608520837 302.1025108849044 12.207436356620342 CELEBRATION 1684 54 779502.0 8.421949954622066 15.957330320972828 144262952 20.15281582952816 7.990276797616247 9.774903061906672 8.161151060594346 1

In [0]:
%sql
SELECT *
FROM gold_calendar
ORDER BY date
LIMIT 100;

date year month day day_of_week week_of_year is_weekend is_payday is_earthquake_period 2013-01-01 2013 1 1 Tue 1 0 0 0 2013-01-02 2013 1 2 Wed 1 0 0 0 2013-01-03 2013 1 3 Thu 1 0 0 0 2013-01-04 2013 1 4 Fri 1 0 0 0 2013-01-05 2013 1 5 Sat 1 1 0 0 2013-01-06 2013 1 6 Sun 1 1 0 0 2013-01-07 2013 1 7 Mon 2 0 0 0 2013-01-08 2013 1 8 Tue 2 0 0 0 2013-01-09 2013 1 9 Wed 2 0 0 0 2013-01-10 2013 1 10 Thu 2 0 0 0 2013-01-11 2013 1 11 Fri 2 0 0 0 2013-01-12 2013 1 12 Sat 2 1 0 0 2013-01-13 2013 1 13 Sun 2 1 0 0 2013-01-14 2013 1 14 Mon 3 0 0 0 2013-01-15 2013 1 15 Tue 3 0 1 0 2013-01-16 2013 1 16 Wed 3 0 0 0 2013-01-17 2013 1 17 Thu 3 0 0 0 2013-01-18 2013 1 18 Fri 3 0 0 0 2013-01-19 2013 1 19 Sat 3 1 0 0 2013-01-20 2013 1 20 Sun 3 1 0 0 2013-01-21 2013 1 21 Mon 4 0 0 0 2013-01-22 2013 1 22 Tue 4 0 0 0 2013-01-23 2013 1 23 Wed 4 0 0 0 2013-01-24 2013 1 24 Thu 4 0 0 0 2013-01-25 2013 1 25 Fri 4 0 0 0 2013-01-26 2013 1 26 Sat 4 1 0 0 2013-01-27 2013 1 27 Sun 4 1 0 0 2013-01-28 2013 1 28 Mon 5 0 0 0 2013-01-29 2013 1 29 Tue 5 0 0 0 2013-01-30 2013 1 30 Wed 5 0 0 0 2013-01-31 2013 1 31 Thu 5 0 1 0 2013-02-01 2013 2 1 Fri 5 0 0 0 2013-02-02 2013 2 2 Sat 5 1 0 0 2013-02-03 2013 2 3 Sun 5 1 0 0 2013-02-04 2013 2 4 Mon 6 0 0 0 2013-02-05 2013 2 5 Tue 6 0 0 0 2013-02-06 2013 2 6 Wed 6 0 0 0 2013-02-07 2013 2 7 Thu 6 0 0 0 2013-02-08 2013 2 8 Fri 6 0 0 0 2013-02-09 2013 2 9 Sat 6 1 0 0 2013-02-10 2013 2 10 Sun 6 1 0 0 2013-02-11 2013 2 11 Mon 7 0 0 0 2013-02-12 2013 2 12 Tue 7 0 0 0 2013-02-13 2013 2 13 Wed 7 0 0 0 2013-02-14 2013 2 14 Thu 7 0 0 0 2013-02-15 2013 2 15 Fri 7 0 1 0 2013-02-16 2013 2 16 Sat 7 1 0 0 2013-02-17 2013 2 17 Sun 7 1 0 0 2013-02-18 2013 2 18 Mon 8 0 0 0 2013-02-19 2013 2 19 Tue 8 0 0 0 2013-02-20 2013 2 20 Wed 8 0 0 0 2013-02-21 2013 2 21 Thu 8 0 0 0 2013-02-22 2013 2 22 Fri 8 0 0 0 2013-02-23 2013 2 23 Sat 8 1 0 0 2013-02-24 2013 2 24 Sun 8 1 0 0 2013-02-25 2013 2 25 Mon 9 0 0 0 2013-02-26 2013 2 26 Tue 9 0 0 0 2013-02-27 2013 2 27 Wed 9 0 0 0 2013-02-28 2013 2 28 Thu 9 0 1 0 2013-03-01 2013 3 1 Fri 9 0 0 0 2013-03-02 2013 3 2 Sat 9 1 0 0 2013-03-03 2013 3 3 Sun 9 1 0 0 2013-03-04 2013 3 4 Mon 10 0 0 0 2013-03-05 2013 3 5 Tue 10 0 0 0 2013-03-06 2013 3 6 Wed 10 0 0 0 2013-03-07 2013 3 7 Thu 10 0 0 0 2013-03-08 2013 3 8 Fri 10 0 0 0 2013-03-09 2013 3 9 Sat 10 1 0 0 2013-03-10 2013 3 10 Sun 10 1 0 0 2013-03-11 2013 3 11 Mon 11 0 0 0 2013-03-12 2013 3 12 Tue 11 0 0 0 2013-03-13 2013 3 13 Wed 11 0 0 0 2013-03-14 2013 3 14 Thu 11 0 0 0 2013-03-15 2013 3 15 Fri 11 0 1 0 2013-03-16 2013 3 16 Sat 11 1 0 0 2013-03-17 2013 3 17 Sun 11 1 0 0 2013-03-18 2013 3 18 Mon 12 0 0 0 2013-03-19 2013 3 19 Tue 12 0 0 0 2013-03-20 2013 3 20 Wed 12 0 0 0 2013-03-21 2013 3 21 Thu 12 0 0 0 2013-03-22 2013 3 22 Fri 12 0 0 0 2013-03-23 2013 3 23 Sat 12 1 0 0 2013-03-24 2013 3 24 Sun 12 1 0 0 2013-03-25 2013 3 25 Mon 13 0 0 0 2013-03-26 2013 3 26 Tue 13 0 0 0 2013-03-27 2013 3 27 Wed 13 0 0 0 2013-03-28 2013 3 28 Thu 13 0 0 0 2013-03-29 2013 3 29 Fri 13 0 0 0 2013-03-30 2013 3 30 Sat 13 1 0 0 2013-03-31 2013 3 31 Sun 13 1 1 0 2013-04-01 2013 4 1 Mon 14 0 0 0 2013-04-02 2013 4 2 Tue 14 0 0 0 2013-04-03 2013 4 3 Wed 14 0 0 0 2013-04-04 2013 4 4 Thu 14 0 0 0 2013-04-05 2013 4 5 Fri 14 0 0 0 2013-04-06 2013 4 6 Sat 14 1 0 0 2013-04-07 2013 4 7 Sun 14 1 0 0 2013-04-08 2013 4 8 Mon 15 0 0 0 2013-04-09 2013 4 9 Tue 15 0 0 0 2013-04-10 2013 4 10 Wed 15 0 0 0